# Import

These requirements are necessary if you launch this notebook from SageMaker instances

In [1]:
"""!pip install mlflow
!pip install pytorch-lightning
!pip install transformers
!pip install tqdm
!pip install sagemaker

!pip install s3fs
!pip install smdebug"""

'!pip install mlflow\n!pip install pytorch-lightning\n!pip install transformers\n!pip install tqdm\n!pip install sagemaker\n\n!pip install s3fs\n!pip install smdebug'

In [2]:
import sys
sys.path.append('../../../')

import os
import sys
import logging
import argparse
from pathlib import Path
from typing import Any, Dict, Optional

In [3]:
from tqdm.auto import tqdm

import torchmetrics
from torchmetrics.functional import accuracy, f1, auroc

import sagemaker
from sagemaker import get_execution_role
import pytorch_lightning as pl
from pytorch_lightning.loggers import TensorBoardLogger
from pytorch_lightning.core.decorators import auto_move_data
from pytorch_lightning.callbacks import ModelCheckpoint, EarlyStopping
from pytorch_lightning.loggers import MLFlowLogger


import matplotlib.pyplot as plt
from pylab import rcParams
from matplotlib import rc

import pandas as pd

Local constants, regarding the data, MLFlow server, paths, etc..: use them

In [ ]:
from deep.constants import *
from deep.utils import *

In [5]:
%load_ext autoreload
%autoreload 2

# Data

You can use the data you want. We advise the `pandas` format.

In [6]:
DATA_PATH = os.path.join(
    '..', '..', '..', "data", "frameworks_data", 'data_v0.7.1'
)


tot_df = pd.read_csv(os.path.join(DATA_PATH, 'new_columns_train_val.csv')).drop_duplicates()

test_df = pd.read_csv(os.path.join(DATA_PATH, 'new_columns_test_v0.7.1.csv'))

/home/selim/anaconda3/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3146: DtypeWarning: Columns (6) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [7]:
columns = ['excerpt', 'entry_id',
           'sectors',
           'present_prim_tags',
           'pillars_2d',
           'pillars_1d', 
           'impact_capresp_humcond', 
           'need_intervention_risk',
           'context_covid', 
           'displacement_shockevent',
           'access_infcom_casualities'
        ]

tot_df = tot_df[columns]
test_df = test_df[columns]

## Sagemaker Prep

### Session

Configure SageMaker

In [8]:
sess = sagemaker.Session(default_bucket=DEV_BUCKET.name)
role = SAGEMAKER_ROLE
role_arn = SAGEMAKER_ROLE_ARN
tracking_uri = MLFLOW_SERVER

### Bucket upload

You need to upload data to an S3 bucket. 




In [9]:
MLFLOW_SERVER

'http://mlflow-deep-387470f3-1883319727.us-east-1.elb.amazonaws.com/'

In [10]:
sample = False  # To make the computations faster, sample = True.

if sample:
    tot_df = tot_df.sample(n=20_000)
    
job_name = f"pytorch-{formatted_time()}-all-models"  # change it as you prefer
input_path = DEV_BUCKET / 'training' / 'input_data' / job_name  # Do not change this

train_path = str(input_path / 'train.pickle')
val_path = str(input_path / 'val.pickle')


tot_df.to_pickle(train_path, protocol=4)  # protocol 4 is necessary, since SageMaker uses python 3.6
test_df.to_pickle(val_path, protocol=4)

### Estimator Definition

In [11]:
# GPU instances

instances = [
    'ml.p2.xlarge',
    'ml.p3.2xlarge'
]

The hyperparameters are passed as command line arguments to the training script. 

You can add/change them as you like. It's important to keep the `tracking_uri` and the `experiment_name` which are used by MLFlow.

The class `PyTorch` is part of the `SageMaker` python API. The parameters are important and you should probably not change most of them. The ones you may want to change are:

- `instance_type`, specify the instance you want
- `source_dir`, specify your script directory. Try to use global variable as much as possible

In [12]:
from sagemaker.pytorch import PyTorch

instance_type='ml.p3.2xlarge'

hyperparameters={
    'tracking_uri': MLFLOW_SERVER,
    'experiment_name': "pl-all-models-experiments",
    'max_len': 512,
    'epochs': 6,
    'model_name': 'microsoft/xtremedistil-l6-h256-uncased',
    'tokenizer_name': 'microsoft/xtremedistil-l6-h256-uncased',
    'output_length': 256,
    'training_names':','.join(columns[2:]),
    "instance_type": instance_type,
    'beta_f1': 0.8,
    'nb_repetitions': 2
}

estimator = PyTorch(
    entry_point='train_mlflow.py',
    source_dir=str('../../../scripts/training/selim/multiclass-lightning'),
    output_path=str(DEV_BUCKET/'models/'),
    code_location=str(input_path),
    instance_type=instance_type,
    instance_count=1,
    role=role,
    framework_version="1.8",
    py_version="py36",
    hyperparameters = hyperparameters,
    job_name=job_name,
#     train_instance_count=2,
#     train_instance_type="ml.c4.xlarge",
)

In [13]:
fit_arguments = {
    'train': str(input_path),
    'test': str(input_path)
}

In [14]:
# Fit the estimator

estimator.fit(fit_arguments, job_name=job_name)

2021-11-17 12:29:27 Starting - Starting the training job...
2021-11-17 12:29:46 Starting - Launching requested ML instancesProfilerReport-1637152154: InProgress
......
2021-11-17 12:30:57 Starting - Preparing the instances for training.........
2021-11-17 12:32:35 Downloading - Downloading input data...
2021-11-17 12:33:07 Training - Downloading the training image..........................bash: cannot set terminal process group (-1): Inappropriate ioctl for device
bash: no job control in this shell
2021-11-17 12:37:31,836 sagemaker-training-toolkit INFO     Imported framework sagemaker_pytorch_container.training
2021-11-17 12:37:31,858 sagemaker_pytorch_container.training INFO     Block until all host DNS lookups succeed.
2021-11-17 12:37:31,865 sagemaker_pytorch_container.training INFO     Invoking user training script.
2021-11-17 12:37:32,335 sagemaker-training-toolkit INFO     Installing dependencies from requirements.txt:
/opt/conda/bin/python3.6 -m pip install -r requirements.txt


  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
  Created wheel for sagemaker: filename=sagemaker-2.49.1-py2.py3-none-any.whl size=591916 sha256=aec0f0a9792c4730a07b406e0d1627d97ed67f03945e031259dfec4f59de07ce
  Stored in directory: /root/.cache/pip/wheels/4c/af/ea/8ff5943a87155df5b184e54474fbf2b59b75e5c172854643c6
  Created wheel for aiobotocore: filename=aiobotocore-2.0.0-py3-none-any.whl size=50257 sha256=c20f10be757ac2556a807b8a20b565e147b33d7741f85defd4172f45fcbefc77
  Stored in directory: /root/.cache/pip/wheels/b5/38/68/5d90168a8a21f76350f04a302017488a99ff5ebeac93a721a5
  Created wheel for alembic: filename=alembic-1.4.1-py2.py3-none-any.whl size=158155 sha256=6d8ed8a50fe722714d0e1ae78d453a5a2b75060e9b3bf67c5de18e760b31af6b
  Stored in directory: /root/.cache/pip/wheels/e9/7b/aa/e18c983d8236b141f85838ba0f8e4e4ae9bcf7f1e00ff72

  Created wheel for idna-ssl: filename=idna_ssl-1.1.0-py3-none-any.whl size=3160 sha256=cd267a83a4bd7ce519d2a519514dc4d299a875bc144a8de243c312fe7dd01826
  Stored in directory: /root/.cache/pip/wheels/6a/f5/9c/f8331a854f7a8739cf0e74c13854e4dd7b1af11b04fe1dde13
Successfully built sagemaker aiobotocore alembic databricks-cli termcolor wrapt idna-ssl
  Attempting uninstall: typing-extensions
    Found existing installation: typing-extensions 3.10.0.2
    Uninstalling typing-extensions-3.10.0.2:
      Successfully uninstalled typing-extensions-3.10.0.2
  Attempting uninstall: six
    Found existing installation: six 1.16.0
    Uninstalling six-1.16.0:
      Successfully uninstalled six-1.16.0
  Attempting uninstall: numpy
    Found existing installation: numpy 1.19.1
    Uninstalling numpy-1.19.1:
      Successfully uninstalled numpy-1.19.1
  Attempting uninstall: botocore
    Found existing installation: botocore 1.21.63
    Uninstalling botocore-1.21.63:
      Successfully uninstalled bot

[2021-11-17 12:40:12.882 algo-1:80 INFO utils.py:27] RULE_JOB_STOP_SIGNAL_FILENAME: None
[2021-11-17 12:40:12.920 algo-1:80 INFO profiler_config_parser.py:102] User has disabled profiler.
[2021-11-17 12:40:12.921 algo-1:80 INFO json_config.py:91] Creating hook from json_config at /opt/ml/input/config/debughookconfig.json.
[2021-11-17 12:40:12.921 algo-1:80 INFO hook.py:201] tensorboard_dir has not been set for the hook. SMDebug will not be exporting tensorboard summaries.
[2021-11-17 12:40:12.922 algo-1:80 INFO hook.py:255] Saving to /opt/ml/output/tensors
[2021-11-17 12:40:12.922 algo-1:80 INFO state_store.py:77] The checkpoint config file /opt/ml/input/config/checkpointconfig.json does not exist.
[2021-11-17 12:40:13.145 algo-1:80 INFO hook.py:594] name:model.l0.embeddings.word_embeddings.weight count_params:7813632
[2021-11-17 12:40:13.145 algo-1:80 INFO hook.py:594] name:model.l0.embeddings.position_embeddings.weight count_params:131072
[2021-11-17 12:40:13.145 algo-1:80 INFO hook.

#015Validation sanity check: 0it [00:00, ?it/s]#015Validation sanity check:   0%|          | 0/2 [00:00<?, ?it/s]#015                                                              #015#015Training: 99it [00:00, ?it/s]#015Training:   0%|          | 0/7586 [00:00<?, ?it/s]#015Epoch 0:   0%|          | 0/7586 [00:00<?, ?it/s] #015Epoch 0:   0%|          | 30/7586 [00:03<14:43,  8.56it/s]#015Epoch 0:   0%|          | 30/7586 [00:03<14:43,  8.56it/s, loss=2.28, v_num=0, val_loss_epoch=0.699, train_loss=1.740]#015Epoch 0:   1%|          | 60/7586 [00:06<14:28,  8.67it/s, loss=2.28, v_num=0, val_loss_epoch=0.699, train_loss=1.740]#015Epoch 0:   1%|          | 60/7586 [00:06<14:28,  8.67it/s, loss=1.8, v_num=0, val_loss_epoch=0.699, train_loss=1.320] #015Epoch 0:   1%|          | 90/7586 [00:10<14:13,  8.78it/s, loss=1.8, v_num=0, val_loss_epoch=0.699, train_loss=1.320]#015Epoch 0:   1%|          | 90/7586 [00:10<14:13,  8.78it/s, loss=1.87, v_num=0, val_loss_epoch=0.699, train_loss=2.110]#015E

...

on_validation_epoch_start          #011|  1.3092e-05     #011|1              #011|  1.3092e-05     #011|  0.00051868     #011|
on_epoch_start                     #011|  1.3015e-05     #011|1              #011|  1.3015e-05     #011|  0.00051563     #011|
on_epoch_end                       #011|  1.292e-05      #011|1              #011|  1.292e-05      #011|  0.00051186     #011|
on_validation_end                  #011|  1.164e-05      #011|1              #011|  1.164e-05      #011|  0.00046115     #011|
#015Finding best initial lr: 100%|██████████| 100/100 [00:10<00:00,  9.26it/s]#033[AFIT Profiler Report
Action                             #011|  Mean duration (s)#011|Num calls      #011|  Total time (s) #011|  Percentage %   #011|
--------------------------------------------------------------------------------------------------------------------------------------
Total                              #011|  -              #011|_              #011|  13.929         #011|  100 %          #01

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
/opt/conda/lib/python3.6/site-packages/pytorch_lightning/trainer/deprecated_api.py:152: LightningDeprecationWarning: `Trainer.running_sanity_check` has been renamed to `Trainer.sanity_checking` and will be removed in v1.5.
  "`Trainer.running_sanity_check` has been renamed to `Trainer.sanity_checking` and will be removed in v1.5."
#015                                                                          #015#033[AEpoch 0, global step 1528: val_loss reached 0.16441 (best 0.16441), saving model to "/opt/ml/model/model_need_intervention_risk.ckpt" as top 1
Epoch 1, global step 3056: val_loss was not in top 1
Epoch 2, global step 4584: val_loss reached 0.15778 (best 0.15778), saving model to "/opt/ml/model/model_need_intervention_risk.ckpt" as top 1
Epoch 3, global step 6112: val_loss was not in top 1
Epoch 4, global step 7640: val_loss reached 0.14897 (best 0.14897), saving model to "/opt/ml/model/model_need_intervention_risk.ckpt" as top 1
Ep

#015100%|██████████| 13/13 [00:01<00:00,  8.72it/s]#033[A#01514it [00:01,  9.02it/s]                        
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
Using native 16bit precision.
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
FIT Profiler Report
Action                             #011|  Mean duration (s)#011|Num calls      #011|  Total time (s) #011|  Percentage %   #011|
--------------------------------------------------------------------------------------------------------------------------------------
Total                              #011|  -              #011|_              #011|  1.0452         #011|  100 %          #011|
--------------------------------------------------------------------------------------------------------------------------------------
evaluation_step_and_end            #011|  0.01578        #011|2              #011|  0.03156        #011|  3.0194         #011|
validation_step                    #011|  0.015565       #011|2          

#015Finding best initial lr: 100%|██████████| 100/100 [13:51<00:00,  8.32s/it]



2021-11-18 06:23:03 Uploading - Uploading generated training modelProfilerReport-1637152154: IssuesFound

2021-11-18 06:33:50 Completed - Training job completed
Training seconds: 64875
Billable seconds: 64875
